In [1]:
import os
import nltk
import json
import pickle
import re
import string
import pandas as pd
import numpy as np

In [2]:
#nltk.download()

In [3]:
features=['title', 'id', 'release_date', 'lyrics']

In [4]:
df=pd.DataFrame()
for dirname, _, filenames in os.walk('data\json files'):
    for filename in filenames:
        with open(os.path.join(dirname, filename)) as f:
            aux = json.load(f)
            df_tmp=pd.DataFrame()
            Artist= np.full((len(aux['songs'])), aux['name'])
            df_tmp['artist']=Artist
            for f in features:
                col=[song[f] for song in aux['songs']]
                df_tmp[f]=col
            df=pd.concat([df,df_tmp]).reset_index(drop=True)

In [5]:
df

artist                              title       id release_date  \
0     Ariana Grande                     ​thank u, next  4063065   2018-11-03   
1     Ariana Grande                            7 rings  4067762   2019-01-18   
2     Ariana Grande                    ​God is a woman  3681280   2018-07-13   
3     Ariana Grande                       Side To Side  2457495   2016-05-20   
4     Ariana Grande             ​​no tears left to cry  3649172   2018-04-20   
...             ...                                ...      ...          ...   
5853   Taylor Swift              Welcome Back Grunwald  6226864         None   
5854   Taylor Swift  Tolerate it (Polskie Tłumaczenie)  6315848   2020-12-11   
5855   Taylor Swift                           Find you  6209316         None   
5856   Taylor Swift                             Static  6371365         None   
5857   Taylor Swift              Clean - Türkçe Çeviri  6387638   2014-10-27   

                                                 lyrics  
0     [Verse 1]\nThought I'd end up with Sean\nBut h...  
1     [Verse 1]\nYeah, breakfast at Tiffany's and bo...  
2     [Chorus]\nYou, you love it how I move you\nYou...  
3     [Intro: Ariana Grande & Nicki Minaj]\nI've bee...  
4     [Intro]\nRight now, I'm in a state of mind\nI ...  
...                                                 ...  
5853  Turn WYCD on\nYou're\nOn your Grunwald\nBack f...  
5854  [Zwrotka 1]\nSiedzę i patrzę jak czytasz z gło...  
5855  Trying just like they say\nJust taking the ste...  
5856                             *static for 8 seconds*  
5857  [Verse 1]\nKuraklık en kötüsüydü(Oh-oh-oh)\nBe...  

[5858 rows x 5 columns]

In [6]:
tmp=[]
#tags=['remix','Remix', 'REMIX', 'live', 'Live', 'Acoustic',' Version', ' ver', 'version', 'Demo', 'demo' , 'Reprise', 'Copy', 'Mix','Edit']
tags=['remix', 'live','club', 'acoustic',' version', ' ver', 'demo', 'reprise', 'copy', 'mix','edit']
#tags=['club']
for title in df['title']:
    for tag in tags:
        r=re.search(tag,title.lower())
        #r=title.find(tag)
        if r != None:
            tmp.append(title)

In [7]:
tmp

['34+35 (Remix)',
 '34+35 (Remix)',
 '7 rings (Remix)',
 '7 rings (Remix)',
 'Into You (Alex Ghenea Remix)',
 'Into You (Alex Ghenea Remix)',
 'The Way (Spanglish Version)',
 'The Way (Spanglish Version)',
 'Somewhere Over the Rainbow (Live From Manchester)',
 'Bad to You (Demo)',
 'The Wizard and I (Live)',
 'The Way (Fabolous Remix)',
 'The Way (Fabolous Remix)',
 '\u200bmy heart belongs to daddy (live)',
 'The Way (Spanglish Version) [feat. J Balvin]',
 'The Way (Spanglish Version) [feat. J Balvin]',
 'Be Alright (Demo)',
 'Quit (Demo)',
 '7 rings (live)\u200b',
 '\u200bthank u, next (live)',
 '\u200bimagine / My Favorite Things / 7 rings / thank u, next (Live at the 62nd Grammy Awards)',
 'Leave Me Lonely (Reprise)',
 '\u200bbreak your heart right back (live)',
 'Problem (Spanglish Version)',
 'Problem (Spanglish Version)',
 '\u200bside to side (live)',
 'Santa Tell Me (Dirty Version)',
 'Santa Tell Me (Dirty Version)',
 '\u200bthe light is coming (Demo)',
 '\u200bgod is a woman (l

In [8]:
for title in tmp:
    df= df[df.title != title].reset_index(drop=True)

In [9]:
print(df[df.id==tmp[9]].values)

[]


In [10]:
for f in features:
    print("number null value of {}: ".format(f),sum(df[f].isnull()))
    
df.dropna(subset = ["lyrics"], inplace=True)

number null value of title:  0
number null value of id:  0
number null value of release_date:  1362
number null value of lyrics:  7


In [11]:
tmp=[]
for idx, lyric in zip(df.id, df.lyrics):
    #if (len(lyric.split("\n"))<6 and re.search('\[(.*?)\]', lyric)==None) or len(lyric)<100: 
    if len(lyric.split("\n"))<6 and re.search('\[(.*?)\]', lyric) is None:
        tmp.append(lyric)

In [12]:
tmp

['Lyrics from Snippet:\n\n... Close to the light, yeah\nDidn’t get to say goodbye to you\nBut I feel like I never ...',
 'Lyrics for this song have yet to be released. Please check back once the song\u2005has\u2005been released',
 'Lyrics will be available upon release. Stay tuned!',
 "I thought that I was a hopeless romantic\nI thought that I was a hopeless romantic\nI really thought that I'd be like my grandparents\nI thought that I was a hopeless romantic",
 'TBA',
 '          \n            Lyrics for this song have yet to be released. Please check back once the song has been released.\n          \n        ',
 'Ariii , Kim?........',
 '          \n            Lyrics for this song have yet to be released. Please check back once the song has been released.\n          \n        ',
 '          \n            Lyrics for this song have yet to be released. Please check back once the song has been released.\n          \n        ',
 'Released in 2019',
 '          \n            Lyrics for thi

In [13]:
df.dropna(subset = ["lyrics"], inplace=True)
tmp=[]
for idx,lyric in zip(df.id, df.lyrics):
    if (len(lyric.split("\n"))<6 and re.search('\[(.*?)\]', lyric)==None) or len(lyric)<100: 
        tmp.append(idx)
for i in tmp:
    df=df[df.id!=i]
df=df.reset_index(drop=True)

# Preprocessing

In [14]:
import preprocess
clean= preprocess.Preprocessing(Pipeline=['lemmatizer'])

In [15]:
lyrics= np.array([clean.Preprocess(lyric) for lyric in df.lyrics])

. thought i would end up with sean. but he was not a match. wrote some songs about ricky. now i listen and laugh. even almost got married. and for pete, i am so thankful. wish i could say, "thank you" to malcolm. because he was an angel. . one taught me love. one taught me patience. and one taught me pain. now, i am so amazing. say i have loved and i have lost. but that is not what i see. so, look what i got. look what you taught me. and for that, i say. . thank you, next (next). thank you, next (next). thank you, next. i am so fuckin' grateful for my ex. thank you, next (next). thank you, next (next). thank you, next (next). i am so fuckin'. . spend more time with my friends. i is not worried about nothin'. plus, i met someone else. we having better discussions. i know they say i move on too fast. but this one going to last. because her name is ari. and i am so good with that (so good with that). . she taught me love (love). she taught me patience (patience). how she handles pain (pai

. lacigam gnihtemos od ot. thgin laiceps ruoy s'thginot tub. . some days, things just take. way too much of my energy. i look up and the whole room's spinning. you take my cares away. i can so over-complicate, people tell me to medicate. . feel my blood runnin', swear the sky's fallin'. i know that all this shit's fabricated, mmm. time goes by and i can not control my mind. do not know what else to try, but you tell me every time. . just keep breathin' and breathin' and breathin' and breathin'. and oh, i got keep, keep on breathin'. just keep breathin' and breathin' and breathin' and breathin'. and oh, i got keep, keep on breathin', mmm-mmm. . sometimes it is hard to find. find my way up into the clouds. tune it out, they can be so loud. you remind me of a time. when things were not so complicated. all i need is to see your face. . feel my blood runnin', swear the sky's fallin'. i know that all this shit's fabricated, mmm. time goes by and i can not control my mind. do not know what el

. if you take too long to hit me back. i can not promise you how ill react. but all i can say is at least i will wait for you. lately, i have been on a roller coaster. tryna get a hold of my emotions. but all that i know is i need you close. . ima scream and shout for what i love. passionate, but i do not give no fucks. i admit that i am a lil' messed up. but i can hide it when i am all dressed up. i am obsessive and i love too hard. good at overthinking with my heart. how you even think it got this far, this far?. . and i can be needy, way too damn needy. i can be needy, tell me how good it feels to be needed. i can be needy, so hard to please me. i know it feels so good to be needed. . sorry if i am up and down a lot (yeah). sorry that i think i am not enough. and sorry if i say sorry way too much. you can go ahead and call me selfish (selfish). but after all this damage, i can not help it (help it). but what you can trust is i need your touch. . ima scream and shout for what i love.

. mmm, last night, boy, i met you, yeah. when i was asleep ('sleep). you are such a dream to me, mmm, woah. and it was on a day like this, yeah. if you can believe, if you can believe (if you can believe). mmm, you are such a dream to me. . before you speak, do not move. because i do not wanna wake up. wake up, wake up, wake up. do not wanna wake up, oh. wake up, wake up, wake up. boy, you are such a dream. if you can believe, babe. boy, you are such a dream to me. . "excuse me, um, i love you". i know that is not the way to start a conversation, trouble. i watch them other girls when they come and bug you. but i felt like i knew you, so i just wanted to hug you. plus you do not know your way around. you can stop your playing now. all your worries, lay 'em down, shh, do not say it loud. is this real, baby?. (bum, bum, bum, bum, bum, bum, bum, bum, bum, bum, bum). you are like: "i love youwho starts a conversation like that?" nobody, but i do. but you are not a picture, i can not cut yo

. i am so into you, i can barely breathe. and all i wanna do is to fall in deep. but close is not close enough 'til we cross the line, hey yeah. so name a game to play and i will roll the dice, hey. . oh baby, look what you started. the temperature's rising in here. is this going to happen?. been waiting and waiting for you to make a move. before i make a move. . so, baby, come light me up, and, baby, i will let you on it. a little bit dangerous, but, baby, that is how i want it. a little less conversation and a little more touch my body. because i am so into you, into you, into you. got everyone watchin' us, so, baby, let us keep this secret. a little bit scandalous, but, baby, do not let them see it. a little less conversation and a little more touch my body. because i am so into you, into you, into you (ooh, yeah). . this could take some time, hey. made too many mistakes. better get this right, right, baby. . oh, baby, look what you started. the temperature's rising in here. is this

...

8/20/2019 upload. welcome video. "dear lover, i can not talk to you when you are like this". taylor swift -"lover". benjaminfrancis leftwich -"4am in london". dixie chicks - "easysilence". dermot kennedy - "outnumbered". lykke li - "bad woman". jimmy eat world - "for me this is heaven". lana del rey - "looking for america". donna lewis - "i love you always forever". nicki minaj - "come see about me". blondie - "maria". taylor swift - "you need to calm down". clairo - "alewife". phil collins - "can't stop loving you". annie lennox - "no more 'i love you's'". taylor swift - "the archer". liz phair - "why can not i?". okay kaya - "believe". james blake - "into the red". kesha - "past lives". taylor swift - "me!" (feat. brendon urie)
. you turn your dial to 93.7. broadway acts like he is 11. self-proclaimed. say's he is the worst mistake ever to land in michigan. i am just a singer of country songs. just trying to play guitar and not do no wrong. but if you listen to just one thing i say. 

. the buttons of my coat were tangled in my hair. in doctor's office lighting, i didn'ttellyou i wasscared. that was the first time wewere there. holy orange bottles, each night, i pray to you. desperatepeoplefindfaith, so nowi pray tojesus too. and i say to you.... . ooh-ah. soon, you will get better. ooh-ah. soon, you will get better. ooh-ah. you will get better soon. because you have to. . i know delusion when i see it in the mirror. you like the nicer nurses, you make the best of a bad deal. i just pretend it is not real. i will paint the kitchen neon, i will brighten up the sky. i know i will never get it, there is not a day that i will not try. and i say to you.... . ooh-ah. soon, you will get better. ooh-ah. soon, you will get better. ooh-ah. you will get better soon. because you have to. . and i hate to make this all about me. but who am i supposed to talk to?. what am i supposed to do. if there is no you?. . this will not go back to normal, if it ever was. it is been years of 

romeo, save me, i have been feeling so alone. i keep -screech- waiting for you but you never come. is this in my head? i do not know what to think. he knelt to the ground and pulled out a ring, and said. "marry me, juliet, you will never have to be alone. i love you, and that is all i really know. i talked to your dad, go pick out a white dress. it is a love story, baby, just say "yes". oh, oh. because we were both young when i first saw you
. should have been different but. it was not different, was it. same old story, dear john. and so long. should have fit like a glove. should have fit like a ring. like a diamond ring. a token of true love. should have all worked out. but it didn't. she should be here now. but she isn't. . there is your trouble. there is your trouble. you keep seeing double. with the wrong one. you can not see i love you. you can not see she doesn't. but you just keep holding on. there is your trouble. . so now you are thinking 'bout. all you are missing how. deep y

. one, two, one. . my only one. my smoking gun. my eclipsed sun. this has broken me down. my twisted knife. my sleepless night. my winless fight. this has frozen my ground. . stood on the cliffside screaming, "give me a reason". your faithless love's the only hoax i believe in. do not want no other shade of blue but you. no other sadness in the world would do. . my best laid plan. your sleight of hand. my barren land. i am ash from your fire. . stood on the cliffside screaming, "give me a reason". your faithless love's th only hoax i believe in. do not want no othr shade of blue but you. no other sadness in the world would do. . you know i left a part of me back in new york. you knew the hero died so what is the movie for?. you knew it still hurts underneath my scars. from when they pulled me apart. you knew the password so i let you in the door. you knew you won so what is the point of keeping score?. you knew it still hurts underneath my scars. from when they pulled me apart. but wha

. jestem jak woda tej nocy. kiedy twoja d przybia noc. szorstka na zewntrz. ale przecie mnie jak n. i gdyby sytuacja bya czarno-biaa. to nigdybym nie wiedziaa z twojego wyrazu twarzy. zagubiona w twoim prdzie jakbezcennewino. [refren}. imwicej mwisz, tymmniej wiem. gdziekolwiek zabdzisz,tam pod. bagam, eby mnie wzi za rk. zrujnowa moje plany - to mj facet. . ycie byo jak wierzba ugita przez twj wiatr. gowa na poduszce, czuam jak wkradae si. jakby by mityczn rzecz. jakby by trofeum. to byaby jedyna nagroda, dla ktrej mogabym oszukiwa. . i am wicej mwisz, tym mniej wiem. gdziekolwik zabdzisz, tam pod. bagam, eby mnie wzi za rk. zrujnowa moje plany - to mj fact. . ycie byo jak wierzb ugita przez twj wiatr. wykluczyli mnie niejeden raz. ycie byo jak wierzb ugita przez twj wiatr. ale ja powracam mocniej ni trend z 90-tych lat. . czekaj na sygna a spotkam ci po zmroku. poka mi miejsca, gdzie zrobili ci blizny. teraz sytuacja jest czarno-biaa. zgaduj, e powinnam bya to wiedzie przez twj wyraz

In [16]:
lyrics

array(['thought would end sean not match write song ricky listen laugh even almost got married pete thankful wish could say thank malcolm angel one taught love one taught patience one taught pain amazing say love lose not see look got look teach say thank next next thank next next thank next fuckin grateful ex thank next next thank next next thank next next fuckin spend time friend not worry nothin plus met someone else good discussion know say move fast one go last name ari good good teach love love teach patience patience handle pain pain shits amazing yeah amazing love lose yeah yeah not see yeah yeah look found yeah yeah not need searching say thank next thank next thank next thank next thank next thank fuckin grateful ex thank next thank next thank next said thank next thank next next fuckin grateful ex thank next thank next thank next fuckin one day walk aisle hold hand mama thank dad grow drama wan na real bad go make shit last god forbid something happen least song smash song s

In [25]:
len(clean.lemmatizer.lemmatizer.word_lemma_dict.keys())

23035

In [18]:
tokenize_lyric=[]
from tqdm import tqdm
for lyric in tqdm(lyrics):
    tokenize_lyric.append(lyric.split())


100%|███████████████████████████████████████████████████████████████████████████| 3833/3833 [00:00<00:00, 20504.01it/s]


In [20]:
id= np.array([id for id in df.id])
for i in range(len(df)):
    tokenize_lyric[i].append(f"-->{id[i]}")

In [21]:
from rank_bm25 import BM25Okapi, BM25Plus

In [22]:
bm25 = BM25Plus(tokenize_lyric)

In [23]:
def bm25okapi_search(tokenized_query, bm25, corpus, n_results = 1):
    """
    Function that takes a tokenized query and prints the first 100 words of the 
    n_results most relevant results found in the corpus, based on the BM25
    method.
    
    Parameters
    ----------
    @param tokenized_query: list, array-like
        A valid list containing the tokenized query.
    @param bm25: BM25 object,
        A valid object of type BM25 (BM25Okapi or BM25Plus) from the library
        `rank-bm25`, initialized with a valid corpus.
    @param corpus: list, array-like
        A valid list containing the corpus from which the BM25 object has been 
        initialized. As returned from function read_corpus().
    @param n_results: int, default = 1
        The number of top results to print.
    """
    
    # We skip checking validity of arguments for now... We assume the user 
    # knows what they're doing.
    
    # Get top results for the query
    top_results = bm25.get_top_n(tokenized_query, corpus, n = n_results)
    
    # Take words from each result
    top_results_id = [' '.join(top_result).split("-->")[-1] 
                             for top_result in top_results]
    
    # Return results
    return top_results_id

In [142]:
corpus= "The map that leads to you"

In [143]:
corpus=clean.Preprocess(corpus)
corpus=[corpus.split(" ")]


In [144]:
corpus

[['map', 'leads']]

In [147]:
rank=bm25okapi_search(corpus[0], bm25, tokenize_lyric, n_results= 5)

In [148]:
for i in rank:
    print(df[df.id==int(i)].title)

2663    Maps
Name: title, dtype: object
2307    Passenger
Name: title, dtype: object
3526    ​’tis the damn season
Name: title, dtype: object
2387    Watch Me Walk Away
Name: title, dtype: object
1413    Little Bird
Name: title, dtype: object


In [33]:
query= "we don't talk anymore"

In [ ]:
import nltk
from nltk.corpus import wordnet

In [ ]:
print(negation_handler(nltk.word_tokenize(query)))

In [ ]:
tokens= nltk.word_tokenize(query)

In [ ]:
def negation_handler(sentence):
    temp = int(0)
    for i in range(len(sentence)):
        if sentence[i-1] in ['not',"n't"]:
            antonyms = []
            for syn in wordnet.synsets(sentence[i]):
                syns = wordnet.synsets(sentence[i])
                w1 = syns[0].name()
                temp = 0
                for l in syn.lemmas():
                    if l.antonyms():
                        antonyms.append(l.antonyms()[0].name())
                max_dissimilarity = 0
                for ant in antonyms:
                    syns = wordnet.synsets(ant)
                    w2 = syns[0].name()
                    syns = wordnet.synsets(sentence[i])
                    w1 = syns[0].name()
                    word1 = wordnet.synset(w1)
                    word2 = wordnet.synset(w2)
                    if isinstance(word1.wup_similarity(word2), float) or isinstance(word1.wup_similarity(word2), int):
                        temp = 1 - word1.wup_similarity(word2)
                    if temp>max_dissimilarity:
                        max_dissimilarity = temp
                        antonym_max = ant
                        sentence[i] = antonym_max
                        sentence[i-1] = ''
    while '' in sentence:
        sentence.remove('')
    return sentence

In [ ]:
wordnet.synsets('hello')

In [18]:
from nltk.stem import PorterStemmer, WordNetLemmatizer

In [249]:
normalise_text("i could not do that",'lemma')

['i could not do that']


TypeError: sequence item 0: expected str instance, list found

In [1]:
import lemma

In [2]:
lem= lemma.LemmatizationWithPOSTagger()

In [3]:
tmp=lem.lemmatize(["he does They would appreciate discussing ways to enhance the airport user's experience"])

In [4]:

from nltk.corpus import wordnet

In [7]:
lem.lemmatize(['he was running as a child'])

['he be run as a child']

In [12]:
len(lem.lemmatizer.word_lemma_dict.keys())

23035